<a href="https://colab.research.google.com/github/pri-nitta/FIAP_IA/blob/main/Criando_um_modelo_com_embeddings_para_produtos_de_ecommerce.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
import pandas as pd
import gensim
from gensim.models import Word2Vec
import re
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import random
import time
import string
import unicodedata
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
from sklearn import svm
from sklearn import metrics
import multiprocessing

In [3]:
df = pd.read_csv("https://dados-ml-pln.s3-sa-east-1.amazonaws.com/produtos.csv", delimiter=";", encoding='utf-8')
df.dropna(inplace=True) #retirando os nulos
df["texto"] = df['nome'] + " " + df['descricao']
df = df.loc[:, ['categoria', 'texto']]
df.head(3)

categoria                                              texto
0     livro   O Hobbit - 7ª Ed. 2013  Produto NovoBilbo Bol...
1     livro   Livro - It A Coisa - Stephen King  Produto No...
2     livro   Box  As Crônicas De Gelo E Fogo  Pocket  5 Li...

In [4]:
df.shape

(2916, 2)

In [5]:
df = shuffle(df) #para auxiliar no treinamento e não deixar a categoria livro no começo
df = df.reset_index(drop = True)
df.head()

categoria                                              texto
0      livro   Livro Serial Killers - Anatomia Do Mal Frete ...
1  maquiagem   Maleta Grande Maquiagem Original Rubyrose Avo...
2  brinquedo   Coleção Kit 18 Miniaturas Super Mario Bros - ...
3      livro   Ebook - O Homem Que Buscava Sua Sombra -  Dav...
4       game   Call Of Duty Black Ops Collection Xbox 360 1,...

In [6]:
df['categoria'].value_counts()

categoria
livro        838
maquiagem    788
brinquedo    668
game         622
Name: count, dtype: int64

In [10]:
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('punkt_tab')

#remover os acentos
def normalize_accents(text):
    return unicodedata.normalize("NFKD", text).encode("ASCII", "ignore").decode("utf-8")

#deixar em caixa baixa
def normalize_str(text):
    text = text.lower()
    text = remove_punctuation(text)
    text = normalize_accents(text)
    text = re.sub(re.compile(r" +"), " ",text)
    return " ".join([w for w in text.split()])

#remover as pontuações
def remove_punctuation(text):
    punctuations = string.punctuation
    table = str.maketrans({key: " " for key in punctuations})
    text = text.translate(table)
    return text

#remover as stop words/ palavras q não são relevante para o contexto
def tokenizer(text):
    stop_words = nltk.corpus.stopwords.words("portuguese") # portuguese, caso o dataset seja em português
    if isinstance(text, str):
        text = normalize_str(text)
        text = "".join([w for w in text if not w.isdigit()])
        text = word_tokenize(text)
        text = [x for x in text if x not in stop_words]
        text = [y for y in text if len(y) > 2]
        return [t for t in text] #lista de palavras
    else:
        return None

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [11]:
df['texto_Treated'] = df['texto'].apply(tokenizer)

In [12]:
df.head()
#texto já tratado

categoria                                              texto  \
0      livro   Livro Serial Killers - Anatomia Do Mal Frete ...   
1  maquiagem   Maleta Grande Maquiagem Original Rubyrose Avo...   
2  brinquedo   Coleção Kit 18 Miniaturas Super Mario Bros - ...   
3      livro   Ebook - O Homem Que Buscava Sua Sombra -  Dav...   
4       game   Call Of Duty Black Ops Collection Xbox 360 1,...   

                                       texto_Treated  
0  [livro, serial, killers, anatomia, mal, frete,...  
1  [maleta, grande, maquiagem, original, rubyrose...  
2  [colecao, kit, miniaturas, super, mario, bros,...  
3  [ebook, homem, buscava, sombra, david, lagercr...  
4  [call, duty, black, ops, collection, xbox, mid...

In [13]:
# parâmetros do word2vec
dim_vec = 300 #dimensão
min_count = 10 # palavras que apareçam pelo menos 10x no dicionário, evita de pegar palavras raras, que não são representativas
window = 4     # a palavras antes e 4 palavras depois, numero de tokens
num_workers = multiprocessing.cpu_count() #cpu disponíveis no computador
seed = np.random.seed(42) #manter a mesma aleatoriedade

In [14]:
# instância do Word2Vec
modelo = Word2Vec(df["texto_Treated"],
                    min_count = min_count,
                    vector_size = dim_vec,
                    window = window,
                    seed = seed,
                    workers = num_workers,
                    sg = 1) #sg = 0 -> CBOW e sg = 1 -> skipgram

# sg (Skip-gram): Prever as palavras que estão a uma certa distância (contexto) da palavra central (target). frase e palavras central das 4 pra frente e 4 pra trás
# cbow (continuous bag of word): Reconstruir a palavra central (target) com base em um contexto de palavras ao seu redor

In [15]:
print("Tamanho do vocabulário do Word2Vec: ", len(modelo.wv))

Tamanho do vocabulário do Word2Vec:  4802


In [16]:
# exemplos das relações semânticas que o word2vec consegue estabelecer
print(modelo.wv.most_similar('mario'), '\n') # palavra mais similar a 'mario'
print(modelo.wv.similarity('mario', 'game'), '\n') # similaridade entre duas palavras
print(modelo.wv.most_similar(positive = ['mario', 'luigi'], negative = ['game'], topn = 3)) # similaridade considerando exemplos positivos e negativos

[('bros', 0.9555660486221313), ('saiyan', 0.9112106561660767), ('heroes', 0.9092807173728943), ('luigi', 0.9089573621749878), ('sayajin', 0.9084553122520447), ('man', 0.8966885209083557), ('trunks', 0.8934346437454224), ('kai', 0.8868372440338135), ('power', 0.8861839175224304), ('sonic', 0.8856058716773987)] 

0.57343584 

[('trunks', 0.8444252610206604), ('freeza', 0.8371596932411194), ('majin', 0.8270363807678223)]


In [17]:
# Embedding para ser representado por uma frase

def meanVector(model,phrase):
    vocab = list(model.wv.index_to_key) #Retorna uma lista com as palavras que formam o vocabulário do modelo
    phrase = " ".join(phrase) #Junta as palavras numa string só
    phrase = [x for x in word_tokenize(phrase) if x in vocab] #Mantém na variável apenas palavras que estão no dicionário
    #Quando não houver palavra o vector recebe 0 para todas as posições
    if phrase == []:
        vetor = [0.0]*dim_vec
    else:
        #Caso contrário, calcula um vetor com a média do vetor de cada palavra na frase
        vetor = np.mean([model.wv[word] for word in phrase],axis=0)
    return vetor

In [18]:
# Função para retornar as features para inputar no modelo
def createFeatures(base):  #Cria uma função chamada createFeatures que recebe o dataframe como parâmetro
    #Calcula o vetor médio de cada frase presente na base e retorna num formato de lista de listas
    features = [meanVector(modelo,base['texto_Treated'][i])for i in range(len(base))]
    return features

In [19]:
labels = np.array(df['categoria']) # label para cada uma das frases, pegar as categorias

In [20]:
df = createFeatures(df)

In [21]:
df

[array([-7.68324733e-02,  8.06501433e-02, -2.43512280e-02, -1.11209136e-02,
         3.15186270e-02,  7.80411661e-02, -5.77148423e-02, -6.99076205e-02,
        -1.74145699e-02, -9.01057869e-02, -1.72004655e-01,  1.84584074e-02,
        -1.43826440e-01, -1.05895221e-01, -1.22539909e-03,  7.23443553e-02,
        -1.87185798e-02,  5.85405454e-02,  4.82383184e-02, -4.91506495e-02,
        -1.94417968e-01,  4.43923511e-02, -7.63542652e-02,  1.19846620e-01,
         1.68542638e-01, -7.74004161e-02,  1.57642424e-01,  9.98337641e-02,
        -3.82237695e-02, -3.87779400e-02, -7.32166469e-02,  1.45377904e-01,
         1.49458230e-01, -7.08036050e-02, -4.73236181e-02, -1.06762126e-01,
        -9.83473565e-03,  4.67918254e-02,  8.86589810e-02, -8.07173401e-02,
         5.79910241e-02, -2.35803071e-02,  1.85984090e-01, -6.28356934e-02,
        -9.31573957e-02, -3.99866104e-02, -1.15044296e-01,  1.46522177e-02,
         2.92939204e-03,  6.27123341e-02, -7.15043247e-02, -1.13066815e-01,
         1.6

In [22]:
X_train, X_test, y_train, y_test = train_test_split(df, labels, test_size=0.3,random_state=42)
clf = svm.SVC(kernel='rbf') #  utiliza uma função de base radial como kernel.
#SVM com kernel RBF é uma escolha sólida quando se lida com conjuntos de dados complexos e não lineares.
start_time = time.time()
clf.fit(X_train, y_train)
end_time = time.time()
y_pred = clf.predict(X_test)

In [23]:
import datetime
sec = end_time-start_time
print(str(datetime.timedelta(seconds = sec)))

0:00:00.231952


In [24]:
print("Accuracy:",metrics.accuracy_score(y_test, y_pred))

Accuracy: 0.9805714285714285


In [25]:
# Frases fornecidas
frases = ['A O Reilly separou alguns dos melhores insights de especialistas em matéria de programação e membros da indústria para que programadores possam mergulhar profundamente no mais recente do que está acontecendo no mundo da engenharia de software, arquitetura e código aberto.',
          'A Maybelline NY criou um Testador Virtual que te ajuda a escolher a tonalidade do seu corretivo, usando a câmera do seu smartphone. Nessa plataforma, é usado recurso de Inteligência Artificial que identifica através da sua foto, o tom da sua pele, sendo assim, sugere o tom ideal para você usar.',
          'A saga Zelda é uma série de jogos de ação e aventura desenvolvida pela Nintendo, que começou em 1986 com o lançamento de “The Legend of Zelda” para o console NES. Ela é centrada em torno de Link, um herói corajoso e destemido que luta contra forças do mal para salvar a Princesa Zelda e o Reino de Hyrule',
          'Mario Bro Nintendo']

# Criar um DataFrame
data = {'texto_Treated': frases}
df_novo_teste = pd.DataFrame(data)

df_novo_teste['texto_Treated'] = df_novo_teste['texto_Treated'].apply(tokenizer)

# Criação dos vetores de média para o novo teste
features_novo_teste = createFeatures(df_novo_teste)

# Realiza as previsões com o modelo treinado
y_pred_novo_teste = clf.predict(features_novo_teste)
print(y_pred_novo_teste)

['livro' 'maquiagem' 'game' 'game']
